<h2> 🕵🏻 Anomaly Detection: Sensors | VAR </h2>

<br>

<img src="https://www.outsideonline.com/wp-content/uploads/2019/09/03/bikers-and-peds_h.jpg" height=98% width=98% style="margin-left:1%">

# Problem Statement: Sensors

Detect the outliers/anomalies in the experimental dataset. The dataset stores hourly counting series detected by sensors. These sensors count both people riding bikes and pedestrians. Separate volumes are tallied for each travel mode. Wires in a diamond formation in the concrete detect bikes and an infrared sensor mounted on a wooden post detects pedestrians.


[**Reference**](https://towardsdatascience.com/anomaly-detection-in-multivariate-time-series-with-var-2130f276e5e9)

In [1]:
import numpy as np
import pandas as pd
import scipy.stats as stats
import matplotlib.pyplot as plt

from statsmodels.tsa.statespace.sarimax import SARIMAX
from statsmodels.tsa.vector_ar.var_model import VAR

import warnings
warnings.simplefilter('ignore')

# Data Set 

Using a **modified dataset version** of [Seattle Burke Gilman Trail](https://www.kaggle.com/datasets/city-of-seattle/seattle-burke-gilman-trail) (i.e. hosted by the city of Seattle which is part of its open data project). 

The dataset stores hourly counting series detected by sensors. These sensors count both people riding bikes and pedestrians. Separate volumes are tallied for each travel mode. Wires in a diamond formation in the concrete detect bikes and an infrared sensor mounted on a wooden post detects pedestrians.

<img src="https://storage.googleapis.com/static.modelplace.ai/production/model-previews/openvino_person_vehicle_bike_detection_crossroad.gif" height=98% width=98% style="margin-left:1%">

In [2]:
### READ DATA ###

train_hours = 80*7*24  # weeks x hours x days
test_hours = 15*7*24  # weeks x hours x days

df = pd.read_csv('/kaggle/input/seattle-mts-trail-west-of-i-90-bridge/mts-trail-west-of-i-90-bridge.csv', nrows=train_hours+test_hours, parse_dates=['Date'])

print(df.shape)
df.head()

(15960, 6)


Date  MTS Trl West of I-90 Bridge Total  Ped East  Ped West  \
0 2013-12-18 00:00:00                                1.0       0.0       0.0   
1 2013-12-18 01:00:00                                1.0       0.0       0.0   
2 2013-12-18 02:00:00                                3.0       1.0       1.0   
3 2013-12-18 03:00:00                                1.0       1.0       0.0   
4 2013-12-18 04:00:00                                2.0       0.0       0.0   

   Bike East  Bike West  
0        0.0        1.0  
1        0.0        1.0  
2        1.0        0.0  
3        0.0        0.0  
4        2.0        0.0

In [3]:
### FILL NAN ###

df['Ped East'] = df['Ped East'].groupby(df.Date.dt.hour).transform(lambda x: x.fillna(x.median()))
df['Ped West'] = df['Ped West'].groupby(df.Date.dt.hour).transform(lambda x: x.fillna(x.median()))
df['Bike East'] = df['Bike East'].groupby(df.Date.dt.hour).transform(lambda x: x.fillna(x.median()))
df['Bike West'] = df['Bike West'].groupby(df.Date.dt.hour).transform(lambda x: x.fillna(x.median()))
df['BGT West of NE 70th Total'] = df['Ped East'] + df['Ped West'] + df['Bike East'] + df['Bike West']

df['Date'] = pd.to_datetime(df['Date'].dt.date)

In [4]:
### DAILY AGGREGATION ###

df_day = pd.DataFrame()
df_day['Ped East'] = df.groupby(df.Date)['Ped East'].sum()
df_day['Ped West'] = df.groupby(df.Date)['Ped West'].sum()
df_day['Bike East'] = df.groupby(df.Date)['Bike East'].sum()
df_day['Bike West'] = df.groupby(df.Date)['Bike West'].sum()
df_day['Total'] = df.groupby(df.Date)['BGT West of NE 70th Total'].sum()

df_day.index = pd.DatetimeIndex(df_day.index.values, freq=df_day.index.inferred_freq)

In [5]:
### PLOT DAILY DATA ###
import matplotlib.pyplot as plt
import plotly.express as px

#df_day.plot(figsize=(24, 9))

fig = px.line(df, x="Date", y=df.columns[2:6], height=500, width=1200, template='plotly_white')
fig.update_layout(
    title="Examples of daily aggregated time series at our disposal",
    yaxis_title=" ",
    legend_title=" ",
    )

In total, 5 counting series are supplied. 2 related to pedestrian count, 2 related to bike count, and the total which is the sum of the previous series. There are double counters for pedestrians and bikes because two directions of travel are registered.

In [6]:
### TRAIN SPLIT ###

train = df_day[:(train_hours//24)].copy()

train.shape

(560, 5)

In [7]:
### TOTAL COUNT TRAIN AUTOCORR ###

plt.figure(figsize=(16,6), dpi= 1000)
pd.plotting.autocorrelation_plot(train['Total'])

<AxesSubplot:xlabel='Lag', ylabel='Autocorrelation'>

In [8]:
### MONTHLY TRAIN MEAN ###

month_mean_train = train.groupby(train.index.month).mean()

In [9]:
### REMOVE LONG TERM SEASONALITY FROM TRAIN ###

train['Ped East'] = train.apply(lambda x: x['Ped East'] - month_mean_train['Ped East'][x.name.month], axis=1)
train['Ped West'] = train.apply(lambda x: x['Ped West'] - month_mean_train['Ped West'][x.name.month], axis=1)
train['Bike East'] = train.apply(lambda x: x['Bike East'] - month_mean_train['Bike East'][x.name.month], axis=1)
train['Bike West'] = train.apply(lambda x: x['Bike West'] - month_mean_train['Bike West'][x.name.month], axis=1)
train['Total'] = train.apply(lambda x: x['Total'] - month_mean_train['Total'][x.name.month], axis=1)

In [10]:
### TOTAL COUNT TRAIN AUTOCORR ###

plt.figure(figsize=(16,6), dpi= 1000)
pd.plotting.autocorrelation_plot(train['Total'])

<AxesSubplot:xlabel='Lag', ylabel='Autocorrelation'>

Passing to a multivariate approach considering all the series and their interaction in the system.

In [11]:
### TRAIN TEST SPLIT IN MULTIVARIATE CASE ###

train_uni = train['Total'].copy()
test_uni = df_day['Total'][(train_hours//24):].copy()
test_uni = test_uni - test_uni.index.month.map(month_mean_train['Total'])

train.drop('Total', inplace=True, axis=1)

# Vector AutoRegression

<img src="https://miro.medium.com/max/1200/0*YplXpgxXCFhf8x34.jpg" height=98% width=98% style="margin-left:1%">

VAR model is a stochastic process that represents a group of time-dependent variables as a linear function of their own past values and the past values of all the other variables in the group.

Here,

VAR training is computed as before selecting the best order minimizing AIC. The data are standardized in the same way to remove the long term seasonality. Not surprisingly the best model is a VAR(7). After testing the independence and normality of residual data, a Hotelling’s T-squared statistic can be computed to detect the early presence of anomalies:

<img src="https://miro.medium.com/max/640/1*lKy-CgCI4qmS9anrp1QdFw.webp" height=40% width=40% style="margin-left:30%">

<p style="margin-left:7%"> <i> <b> the formula for Hotelling T2. e are the estimated residuals; Sigma is the covariance matrix of e </b> </i> </p>

The application of the T-squared control chart is conducted in two phases: the control limit establishment phase, and the monitoring phase. The first phase focuses on obtaining model residuals so that the calculated control limit can be used in phase two for monitoring the residual process of future anomalies. The control limit for the T-squared control chart is given by:

<img src="https://miro.medium.com/max/828/1*404AbCeKlaRnptda26T5KQ.webp" height=50% width=50% style="margin-left:25%">

<p style="margin-left:35%"> <i> <b> Upper Control Limit statistic </b> </i> </p>


In [12]:
### FIND BEST MULTIVARIATE MODEL ###

AIC = {}
best_aic, best_order = np.inf, 0

for i in range(1,50):
    model = VAR(endog=train)
    var_result = model.fit(maxlags=i)
    AIC[i] = var_result.aic
    
    if AIC[i] < best_aic:
        best_aic = AIC[i]
        best_order = i
        
print('BEST ORDER', best_order, 'BEST AIC:', best_aic)


BEST ORDER 4 BEST AIC: 35.41893067698373


In [13]:
### TRAIN BEST MULTIVARIATE MODEL ###

var = VAR(endog=train)
var_result = var.fit(maxlags=best_order)

var_result.aic

35.41893067698373

In [14]:
### COMPUTE TRAIN T2 METRIC ###

residuals_mean = var_result.resid.values.mean(axis=0)
residuals_std = var_result.resid.values.std(axis=0)

residuals = (var_result.resid.values - residuals_mean) / residuals_std
cov_residuals = np.linalg.inv(np.cov(residuals.T))

T = np.diag((residuals).dot(cov_residuals).dot(residuals.T))

In [15]:
### COMPUTE UCL ###

m = var_result.nobs
p = var_result.resid.shape[-1]
alpha = 0.01

UCL = stats.f.ppf(1-alpha, dfn=p, dfd=m-p) *(p*(m+1)*(m-1)/(m*m-m*p))
UCL

13.510289428754227

👉🏻 Where F represents an F distribution with p and n-p degrees of freedom and alpha significance level. If T2 > UCL, then stop and investigate. The estimated Sigma obtained at the end of phase 1 (together with residuals mean and standard deviation) is used to calculate the T-squared statistic for each new observation.

In [16]:
### PLOT TRAIN T2 METRIC ###

plt.figure(figsize=(16,6), dpi= 1000)
plt.plot(train.index[best_order:], T)
plt.ylabel('T-squared')
plt.axhline(UCL, c='red', linestyle='--')

# Multivariate Anomaly Detection 🕵

<img src="https://miro.medium.com/max/1400/1*dSHTs4h5NQT9vDVkj5sEGA.png" height=40% width=40% style="margin-left:30%">

VAR model extends the univariate autoregressive (AR) model by capturing the linear relations between multiple variables. For each input series, a regression is carried out. The original variables are regressed against their own lagged values and the lagged values of other variables. For our multivariate task, we take into account both bike and pedestrian series.

In a multivariate process system with the presence of serial correlation, we use VAR models to approximate the system and monitor the residuals as a serially independent series. Using a VAR to approximate a linear system is appropriate due to the physical principles of the process dynamics.

In [17]:
### TEST SPLIT IN MULTIVARIATE CASE ###

test = df_day[(train_hours//24-best_order):].copy()
test.drop('Total', inplace=True, axis=1)

test.shape

(109, 4)

In [18]:
### REMOVE LONG TERM SEASONALITY FROM TEST ###

test['Ped East'] = test.apply(lambda x: x['Ped East'] - month_mean_train['Ped East'][x.name.month], axis=1)
test['Ped West'] = test.apply(lambda x: x['Ped West'] - month_mean_train['Ped West'][x.name.month], axis=1)
test['Bike East'] = test.apply(lambda x: x['Bike East'] - month_mean_train['Bike East'][x.name.month], axis=1)
test['Bike West'] = test.apply(lambda x: x['Bike West'] - month_mean_train['Bike West'][x.name.month], axis=1)

In [19]:
### ITERATIVE PREDICTIONS ON TEST DATA ###

pred = []

for i in range(best_order, len(test)):
    
    pred.append(var_result.forecast(test.iloc[i-best_order:i].values, steps=1))
    
pred = np.vstack(pred)
pred.shape

(105, 4)

In [20]:
### COMPUTE TEST T2 METRIC ###

residuals_test = test.iloc[best_order:].values - pred
residuals_test = (residuals_test - residuals_mean) / residuals_std

T_test = np.diag((residuals_test).dot(cov_residuals).dot(residuals_test.T))

In [21]:
### PLOT TEST T2 METRIC ###

plt.figure(figsize=(16,6), dpi= 1000)
plt.plot(test.iloc[best_order:].index, T_test)
plt.ylabel('T-squared')
plt.axhline(UCL, c='red', linestyle='--')

# Conclusion 

✏️ Here, I collected the VAR residuals and used them to build a threshold alert system, which flags an alarm in case of anomalous behaviors.


> *The VAR model has proven to be especially useful for describing the dynamic behavior of economic and financial time series and for forecasting. In addition to data description and forecasting, the VAR model is also used for structural inference and policy analysis. In structural analysis, certain assumptions about the causal structure of the data under investigation are imposed, and the resulting causal impacts of unexpected shocks or innovations to specified variables on the variables in the model are summarized. These causal impacts are usually summarized with impulse response functions and forecast error variance decompositions.*

<img src="https://i.pinimg.com/originals/7d/9b/1d/7d9b1d662b28cd365b33a01a3d0288e1.gif" height=60% width=60% style="margin-left:20%">


